# Извлечение признаков из текстовых данных

In [1]:
import numpy as np
import pandas as pd
import re

from nltk.tokenize import sent_tokenize, word_tokenize
from pymorphy3 import MorphAnalyzer
import torch

In [2]:
def count_elements(nested_array):
    return sum(count_elements(item) if isinstance(item, list) else 1 for item in nested_array)

In [ ]:
# загружаем датасет
df = pd.read_csv('data/Petitions.csv')
texts = df["public_petition_text"]

In [11]:
texts

0                                           снег на дороге
1                      очистить кабельный киоск от рекламы
2        Просим убрать все деревья и кустарники, которы...
3        Неудовлетворительное состояние парадной - надп...
4                                                 Граффити
                               ...                        
59884                             прошу закрасить граффити
59885         Прошу вас отремонтировать пешеходную дорожку
59886    Необходимо демонтировать незаконную рекламную ...
59887    Очень гремит на ветру металлическая часть окна...
59888    Две проблемы в одном:\n1) Незаконные надписи/о...
Name: public_petition_text, Length: 59889, dtype: object

Делим по предложениям (. - splitter)


In [ ]:
print(len(texts))
filtered_texts = texts.apply(lambda text: sent_tokenize(text))
filtered_texts = pd.Series(sum(filtered_texts.tolist(), []))
print(len(filtered_texts))

59889
106453


In [ ]:
filtered_texts

0                                            снег на дороге
1                       очистить кабельный киоск от рекламы
2         Просим убрать все деревья и кустарники, которы...
3                                                Наличной).
4         Неудовлетворительное состояние парадной - надп...
                                ...                        
106448    Необходимо демонтировать незаконную рекламную ...
106449    Очень гремит на ветру металлическая часть окна...
106450    Две проблемы в одном:\n1) Незаконные надписи/о...
106451                                 2) Опора имеет крен.
106452    Просьба провести работы по очистке и выправке/...
Length: 106453, dtype: object

Уберём все лишние символы и оставим только буквы:

In [ ]:
# Оставляем только буквы
filtered_texts = filtered_texts.apply(lambda text: " ".join(re.findall("[а-яА-Я]+", text)))

In [13]:
filtered_texts

0                                            снег на дороге
1                       очистить кабельный киоск от рекламы
2         Просим убрать все деревья и кустарники которые...
3                                                  Наличной
4         Неудовлетворительное состояние парадной надпис...
                                ...                        
106448    Необходимо демонтировать незаконную рекламную ...
106449    Очень гремит на ветру металлическая часть окна...
106450    Две проблемы в одном Незаконные надписи объявл...
106451                                     Опора имеет крен
106452    Просьба провести работы по очистке и выправке ...
Length: 106453, dtype: object

### Токенизация

In [14]:
# Токенизация
tokenize_texts = filtered_texts.apply(lambda text: word_tokenize(text))

# for text in tokenize_texts:
#     for word in text:
#         word.replace('нету', 'нет')

In [15]:
tokenize_texts

0                                        [снег, на, дороге]
1                 [очистить, кабельный, киоск, от, рекламы]
2         [Просим, убрать, все, деревья, и, кустарники, ...
3                                                [Наличной]
4         [Неудовлетворительное, состояние, парадной, на...
                                ...                        
106448    [Необходимо, демонтировать, незаконную, реклам...
106449    [Очень, гремит, на, ветру, металлическая, част...
106450    [Две, проблемы, в, одном, Незаконные, надписи,...
106451                                 [Опора, имеет, крен]
106452    [Просьба, провести, работы, по, очистке, и, вы...
Length: 106453, dtype: object

### Лемматизация

In [ ]:
# лемматизация
ma = MorphAnalyzer()
# берёт наиболее вероятный вариант
lemmatize_texts = tokenize_texts.apply(lambda words: [ma.normal_forms(word)[0] for word in words]) 
print(len(lemmatize_texts))
print(count_elements(lemmatize_texts))

106453
780728


In [23]:
lemmatize_texts

0                                        [снег, на, дорога]
1                 [очистить, кабельный, киоск, от, реклама]
2         [просить, убрать, всё, дерево, и, кустарник, к...
3                                                [наличный]
4         [неудовлетворительный, состояние, парадный, на...
                                ...                        
106448    [необходимо, демонтировать, незаконный, реклам...
106449    [очень, греметь, на, ветер, металлический, час...
106450    [два, проблема, в, один, незаконный, надпись, ...
106451                                 [опора, иметь, крен]
106452    [просьба, провести, работа, по, очистка, и, вы...
Length: 106453, dtype: object

In [ ]:
# Убираем жалобы, в которых только одно слово
lemmatize_texts = pd.Series([text for text in lemmatize_texts if len(text) >= 2])
print(len(lemmatize_texts))
print(count_elements(lemmatize_texts))

97337
772832


In [28]:
symbols = ["?","!",".", ","]

In [29]:
for text in lemmatize_texts:
    for word in text:
        if any(s in word for s in symbols): print(text)

### Удаление стоп-слов

In [33]:
# убираем стоп слова
from nltk.corpus import stopwords

# nltk.download('stopwords')

stopwords = stopwords.words("russian")

print(stopwords)
lemmatized_texts = lemmatize_texts.apply(lambda words: [word for word in words if word not in stopwords])
print(lemmatized_texts)
print(count_elements(lemmatized_texts))

['и', 'в', 'во', 'не', 'что', 'он', 'на', 'я', 'с', 'со', 'как', 'а', 'то', 'все', 'она', 'так', 'его', 'но', 'да', 'ты', 'к', 'у', 'же', 'вы', 'за', 'бы', 'по', 'только', 'ее', 'мне', 'было', 'вот', 'от', 'меня', 'еще', 'нет', 'о', 'из', 'ему', 'теперь', 'когда', 'даже', 'ну', 'вдруг', 'ли', 'если', 'уже', 'или', 'ни', 'быть', 'был', 'него', 'до', 'вас', 'нибудь', 'опять', 'уж', 'вам', 'ведь', 'там', 'потом', 'себя', 'ничего', 'ей', 'может', 'они', 'тут', 'где', 'есть', 'надо', 'ней', 'для', 'мы', 'тебя', 'их', 'чем', 'была', 'сам', 'чтоб', 'без', 'будто', 'чего', 'раз', 'тоже', 'себе', 'под', 'будет', 'ж', 'тогда', 'кто', 'этот', 'того', 'потому', 'этого', 'какой', 'совсем', 'ним', 'здесь', 'этом', 'один', 'почти', 'мой', 'тем', 'чтобы', 'нее', 'сейчас', 'были', 'куда', 'зачем', 'всех', 'никогда', 'можно', 'при', 'наконец', 'два', 'об', 'другой', 'хоть', 'после', 'над', 'больше', 'тот', 'через', 'эти', 'нас', 'про', 'всего', 'них', 'какая', 'много', 'разве', 'три', 'эту', 'моя', 'впр

### Создание матрицы эмбеддингов

In [34]:
from collections import defaultdict

dict_matrix = defaultdict(lambda: defaultdict(int))

for i in range(len(lemmatized_texts)):
    for j in range(1, len(lemmatized_texts[i])):
        dict_matrix[lemmatized_texts[i][j]][lemmatized_texts[i][j-1]] += 1
        dict_matrix[lemmatized_texts[i][j-1]][lemmatized_texts[i][j]] += 1

dict_matrix['стена']

defaultdict(int,
            {'надпись': 564,
             'покраска': 32,
             'краска': 73,
             'участник': 1,
             'подт': 1,
             'ки': 4,
             'подъездный': 1,
             'этаж': 109,
             'прикрутить': 2,
             'граффити': 154,
             'всё': 35,
             'обцарапать': 1,
             'рисунок': 25,
             'скол': 16,
             'потолок': 94,
             'дом': 380,
             'непосредственно': 6,
             'кусок': 9,
             'вид': 6,
             'парадный': 111,
             'грязный': 151,
             'ободрать': 3,
             'реклама': 80,
             'отсутствовать': 6,
             'слева': 4,
             'удалить': 1,
             'состояние': 69,
             'фасадный': 7,
             'мкд': 8,
             'й': 4,
             'около': 20,
             'требовать': 5,
             'дверь': 77,
             'просто': 2,
             'здание': 35,
             'сходить': 1,
  

In [37]:
dict_matrix['кабельный']

defaultdict(int,
            {'очистить': 2,
             'киоск': 39,
             'бесхозный': 1,
             'очистка': 8,
             'канал': 6,
             'стена': 1,
             'надпись': 21,
             'шкаф': 10,
             'возгорание': 1,
             'линия': 3,
             'шахта': 2,
             'порядок': 1,
             'установка': 1,
             'граффити': 8,
             'фасад': 1,
             'проводок': 1,
             'кожух': 1,
             'рукав': 1,
             'этаж': 1,
             'сеть': 4,
             'состояние': 1,
             'привести': 1,
             'ленэнерго': 1,
             'щиток': 5,
             'объявление': 4,
             'коробка': 3,
             'разукомплектовать': 1,
             'лоток': 1,
             'производитель': 1,
             'работа': 1,
             'коричневый': 1,
             'зима': 1,
             'реклама': 1,
             'открытый': 1,
             'открыть': 1,
             'территория': 1,


In [13]:
print(dict_matrix['асфальт']['яма'])
print(dict_matrix['яма']['асфальт'])

45
45


In [41]:
sorted(dict_matrix['погода'].keys())

['бак',
 'бег',
 'болтаться',
 'весь',
 'ветренный',
 'ветреный',
 'влажный',
 'возможный',
 'время',
 'всё',
 'грязный',
 'грязь',
 'дверь',
 'двор',
 'дождливый',
 'зависеть',
 'лужа',
 'любой',
 'минусовый',
 'мокрый',
 'мусор',
 'невозможно',
 'независимо',
 'непригодный',
 'образование',
 'образоваться',
 'окно',
 'осадки',
 'отремонтировать',
 'плай',
 'плохой',
 'плый',
 'подниматься',
 'подойти',
 'позволять',
 'постоянно',
 'представлять',
 'пылевой',
 'пыль',
 'решение',
 'связь',
 'ситуация',
 'скапливаться',
 'скользкий',
 'слева',
 'следующий',
 'смотреть',
 'состояние',
 'стальной',
 'стоить',
 'стоять',
 'судить',
 'сухой',
 'сырой',
 'тащиться',
 'тёплый',
 'холодный',
 'это']

In [42]:
# Сортируем ключи словаря
sorted_keys = sorted(dict_matrix.keys())

# Создаем новый словарь с отсортированными ключами
dict_matrix = {key: dict_matrix[key] for key in sorted_keys}

for dict_key in dict_matrix.keys():
    # Сортируем ключи словаря
    sorted_keys = sorted(dict_matrix[dict_key].keys())
    
    # Создаем новый словарь с отсортированными ключами
    dict_matrix[dict_key] = {key: dict_matrix[dict_key][key] for key in sorted_keys}

print(len(dict_matrix.keys()))
dict_matrix['дорога']

16830


{'аварийность': 1,
 'авиаконструктор': 1,
 'авто': 1,
 'автомобиль': 2,
 'автомобильный': 79,
 'автомойка': 1,
 'адрес': 2,
 'активный': 1,
 'алергия': 1,
 'асфальт': 2,
 'асфальтировать': 1,
 'асфальтироваться': 1,
 'асфальтовый': 3,
 'атлантика': 2,
 'бак': 2,
 'бегать': 1,
 'безопасный': 1,
 'берег': 1,
 'бесхозяйный': 1,
 'бетонный': 1,
 'благополучно': 1,
 'благоустройство': 1,
 'близкий': 2,
 'блок': 2,
 'бобыльский': 1,
 'больший': 3,
 'большой': 3,
 'бордюр': 3,
 'бросить': 1,
 'бугор': 1,
 'валяться': 6,
 'варшавский': 1,
 'ваш': 1,
 'вдоль': 99,
 'веда': 2,
 'ведушие': 1,
 'ведущий': 4,
 'вести': 3,
 'весь': 39,
 'вздыбиться': 1,
 'видно': 2,
 'включая': 1,
 'внутри': 4,
 'внутридворовый': 2,
 'внутридомовый': 1,
 'внутриквартальный': 1,
 'вовремя': 2,
 'вода': 3,
 'водый': 1,
 'воздух': 1,
 'возле': 13,
 'возможно': 1,
 'вокзал': 1,
 'вокруг': 3,
 'вообще': 2,
 'восстановить': 1,
 'впадина': 1,
 'впереди': 1,
 'временной': 2,
 'всё': 6,
 'выбегать': 1,
 'выбоина': 4,
 'выбои

In [45]:
dict_matrix

{'аа': {'номер': 1},
 'ааш': {'дом': 1, 'приложение': 1},
 'аба': {'приямок': 1, 'росреестр': 1, 'яд': 1},
 'абажур': {'лампа': 1, 'прикрепить': 1},
 'абз': {'п': 1},
 'абзац': {'нарушить': 2, 'пункт': 2},
 'абонентский': {'болтаться': 1, 'понимаються': 1, 'почтовый': 3, 'ящик': 1},
 'абп': {'вокруг': 2,
  'деформировать': 2,
  'дом': 1,
  'люк': 1,
  'повреждение': 1,
  'разрушить': 1,
  'разрушиться': 1},
 'абразив': {'механический': 4, 'царапать': 4},
 'абразивный': {'материал': 1},
 'абрамов': {'далее': 5,
  'дом': 2,
  'дора': 10,
  'дору': 1,
  'каждый': 1,
  'кор': 1,
  'м': 1,
  'напротив': 1,
  'нечётный': 1,
  'николай': 1,
  'парадный': 1,
  'пешеходный': 1,
  'подъезд': 1,
  'синий': 1,
  'ситуация': 1,
  'снег': 1,
  'сторона': 1,
  'ул': 1,
  'ф': 4,
  'фёдор': 11,
  'ч': 1},
 'абсолютно': {'батарея': 1,
  'безнаказанный': 1,
  'весь': 2,
  'волновать': 1,
  'всё': 2,
  'вывозить': 1,
  'грязный': 2,
  'дать': 1,
  'действительно': 1,
  'дорожка': 1,
  'ездить': 1,
  'иде

In [49]:
for key in dict_matrix.keys():
    if ((sum(dict_matrix[key].values()) > 10) and len(key)>1):
        print(key, dict_matrix[key].values())

абрамов dict_values([5, 2, 10, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 11, 1])
абсолютно dict_values([1, 1, 2, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1])
авангардный dict_values([1, 1, 10, 1, 2, 1, 13, 1])
аварийка dict_values([1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 3, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1])
аварийность dict_values([1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 5, 1, 1, 2, 1, 13, 1])
аварийный dict_values([1, 1, 1, 1, 5, 1, 1, 1, 1, 1, 1, 3, 6, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 4, 1, 2, 1, 2, 2, 1, 5, 3, 2, 1, 8, 1, 1, 1, 1, 1, 1, 1, 13, 1, 1, 14, 1, 3, 1, 1, 2, 1, 3, 1, 1, 15, 6, 8, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 1, 1, 1, 1, 2, 1, 3, 2, 2, 1, 1, 1, 1, 1, 5, 1, 2, 30, 1, 1, 1, 1, 2, 1, 1, 1, 1, 2, 4, 6, 7, 2, 1, 1, 1, 1, 2, 10, 1, 1, 7, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 3, 1, 2, 1, 3, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 2, 2, 

In [52]:
# удаляем так называмые "выбросы" среди слов
new_dict = {}
for key in dict_matrix.keys():
    if ((sum(dict_matrix[key].values()) > 10) and len(key)>1):
        new_dict[key] = dict_matrix[key]
dict_matrix = new_dict

print(len(dict_matrix.keys()))
dict_matrix.keys()

5181


dict_keys(['абрамов', 'абсолютно', 'авангардный', 'аварийка', 'аварийность', 'аварийный', 'авария', 'август', 'авиаконструктор', 'авиатор', 'авиационный', 'аврора', 'авто', 'автобус', 'автобусный', 'автовладелец', 'автолюбитель', 'автомат', 'автоматически', 'автоматический', 'автомашина', 'автомобилист', 'автомобиль', 'автомобильный', 'автостоянка', 'автотранспорт', 'автотранспортный', 'автохлам', 'агротехнический', 'адекватный', 'административный', 'администрация', 'адмирал', 'адмиралтейский', 'адрес', 'адресация', 'адресный', 'аж', 'азс', 'академик', 'академический', 'аккуратно', 'аккуратный', 'акт', 'активно', 'активный', 'актуализировать', 'актуальный', 'александр', 'александровский', 'алкоголь', 'алкогольный', 'аллея', 'алтайский', 'альпийский', 'алюминиевый', 'аналогично', 'аналогичный', 'аналогия', 'английский', 'антенна', 'антивандальный', 'антипарковочный', 'антисанитария', 'антисанитарный', 'антискользящий', 'антонов', 'ао', 'аппарат', 'апраксин', 'апрель', 'апрельский', 'апт

И мы наконец можем получить нашу матрицу эмбеддингов:

In [55]:
df = pd.DataFrame(dict_matrix, index=dict_matrix.keys()).fillna(0)
df

абрамов  абсолютно  авангардный  аварийка  аварийность  \
абрамов          0.0        0.0          0.0       0.0          0.0   
абсолютно        0.0        0.0          0.0       0.0          0.0   
авангардный      0.0        0.0          0.0       0.0          0.0   
аварийка         0.0        0.0          0.0       0.0          0.0   
аварийность      0.0        0.0          0.0       0.0          0.0   
...              ...        ...          ...       ...          ...   
ярус             0.0        0.0          0.0       0.0          0.0   
яхтенный         0.0        0.0          0.0       0.0          0.0   
ящик             0.0        0.0          0.0       0.0          0.0   
ёлка             0.0        0.0          0.0       0.0          0.0   
ёмкость          0.0        0.0          0.0       0.0          0.0   

             аварийный  авария  август  авиаконструктор  авиатор  ...  январь  \
абрамов            0.0     0.0     0.0              0.0      0.0  ...     0.0   
абсолютно          0.0     0.0     0.0              0.0      0.0  ...     0.0   
авангардный        0.0     0.0     0.0              0.0      0.0  ...     0.0   
аварийка           0.0     0.0     0.0              0.0      0.0  ...     0.0   
аварийность        0.0     0.0     0.0              0.0      0.0  ...     0.0   
...                ...     ...     ...              ...      ...  ...     ...   
ярус               0.0     0.0     0.0              0.0      0.0  ...     0.0   
яхтенный           0.0     0.0     0.0              0.0      0.0  ...     0.0   
ящик               0.0     0.0     0.0              0.0      0.0  ...     0.0   
ёлка               0.0     0.0     0.0              0.0      0.0  ...     0.0   
ёмкость            0.0     0.0     0.0              0.0      0.0  ...     0.0   

             яндекс  яркий  ярко  ярослав  ярус  яхтенный  ящик  ёлка  ёмкость  
абрамов         0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
абсолютно       0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
авангардный     0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
аварийка        0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
аварийность     0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
...             ...    ...   ...      ...   ...       ...   ...   ...      ...  
ярус            0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
яхтенный        0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
ящик            0.0    0.0   0.0      0.0   0.0       0.0  12.0   0.0      0.0  
ёлка            0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  
ёмкость         0.0    0.0   0.0      0.0   0.0       0.0   0.0   0.0      0.0  

[5181 rows x 5181 columns]

In [18]:
df.loc['нужно']

абрамов        0.0
абсолютно      0.0
авангардный    0.0
аварийка       0.0
аварийность    0.0
              ... 
яркий          0.0
ярослав        0.0
яхтенный       0.0
ящик           1.0
ёлка           0.0
Name: нужно, Length: 3627, dtype: float64

In [58]:
df.stack()

абрамов  абрамов        0.0
         абсолютно      0.0
         авангардный    0.0
         аварийка       0.0
         аварийность    0.0
                       ... 
ёмкость  ярус           0.0
         яхтенный       0.0
         ящик           0.0
         ёлка           0.0
         ёмкость        0.0
Length: 26842761, dtype: float64

In [56]:
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import matplotlib.pyplot as plt


# Стандартизация данных
scaler = StandardScaler()
scaled_embeddings = scaler.fit_transform(df)

# Создаем и обучаем модель PCA
pca = PCA()
pca.fit(scaled_embeddings)

PCA()

In [61]:
scaled_embeddings

array([[-0.0351453 , -0.08715988, -0.02500505, ..., -0.03643875,
        -0.04869253, -0.04353288],
       [-0.0351453 , -0.08715988, -0.02500505, ..., -0.03643875,
        -0.04869253, -0.04353288],
       [-0.0351453 , -0.08715988, -0.02500505, ..., -0.03643875,
        -0.04869253, -0.04353288],
       ...,
       [-0.0351453 , -0.08715988, -0.02500505, ...,  2.58867129,
        -0.04869253, -0.04353288],
       [-0.0351453 , -0.08715988, -0.02500505, ..., -0.03643875,
        -0.04869253, -0.04353288],
       [-0.0351453 , -0.08715988, -0.02500505, ..., -0.03643875,
        -0.04869253, -0.04353288]])

In [59]:
pca.n_components_

5181

In [64]:
n = 500

pca = PCA(n)
reduced_embeddings = pca.fit_transform(scaled_embeddings)

reduced_embeddings_df = pd.DataFrame(reduced_embeddings, columns=[f'PC{i+1}' for i in range(n)])
reduced_embeddings_df.index = dict_matrix.keys()
reduced_embeddings_df

PC1       PC2       PC3       PC4       PC5       PC6  \
абрамов     -2.167824  2.774128  0.645414  0.706883  0.687338  0.293411   
абсолютно   -1.888483  0.634621  0.358485  0.254213  0.633303 -0.763772   
авангардный -2.881359  1.788439  0.684032  0.676496 -0.199972  0.046706   
аварийка    -2.056758  0.628170 -0.414661 -0.676322  0.056741 -0.801389   
аварийность -2.465457  1.015577  0.035589  0.051802 -0.007631  0.157161   
...               ...       ...       ...       ...       ...       ...   
ярус        -3.094438  1.546435  0.613532  0.769581 -0.096623 -0.032368   
яхтенный    -2.259362  2.190666  0.732127  0.650516 -0.194278  0.029297   
ящик         9.503228 -7.857116 -3.291486  3.487890  0.656322  3.872341   
ёлка        -2.539037  0.866410  1.201623  0.396024  0.201870 -0.687713   
ёмкость     -2.975393  1.386039  0.745034  0.703419 -0.039945 -0.075109   

                  PC7       PC8       PC9      PC10  ...     PC491     PC492  \
абрамов     -0.232899  0.125882 -0.287602 -0.059639  ...  0.972674  2.503852   
абсолютно   -0.535447  0.194019  0.088726  0.054934  ... -0.030936 -0.162939   
авангардный -0.284402  0.248382 -0.170754 -0.373056  ...  0.057042 -0.005532   
аварийка    -0.582756 -0.359424 -0.020087 -0.568436  ...  0.451848 -1.177414   
аварийность -0.549549  1.115635 -0.367755 -0.895193  ...  0.134774 -0.073004   
...               ...       ...       ...       ...  ...       ...       ...   
ярус        -0.398061  0.226858 -0.154609 -0.564978  ...  0.045530  0.010797   
яхтенный    -0.254020  0.331956 -0.137822 -0.193887  ...  0.043502 -0.056493   
ящик         1.802491 -1.087298  0.220229  0.767087  ...  2.055722 -0.379162   
ёлка         1.072599  1.013498  0.049853 -1.142083  ...  0.190056  0.288682   
ёмкость     -0.072402  0.182207 -0.022567 -0.632771  ... -0.020177  0.014617   

                PC493     PC494     PC495     PC496     PC497     PC498  \
абрамов     -1.011024  2.455147  0.830435 -1.844252 -1.034388  0.631703   
абсолютно   -0.202108  0.191390 -0.130308  0.201746  0.220459 -0.469843   
авангардный -0.116463 -0.016490  0.016316  0.058177  0.000926 -0.129403   
аварийка     1.153140 -0.445216 -0.392335 -1.180905  0.580129 -0.500308   
аварийность -0.154872  0.175023  0.280558  0.380537 -0.115484 -0.096024   
...               ...       ...       ...       ...       ...       ...   
ярус        -0.072109  0.012238  0.021080  0.072358  0.026876 -0.088743   
яхтенный    -0.227974 -0.036700  0.090807  0.148753  0.051623 -0.173419   
ящик        -2.129037 -4.887692 -4.453293  0.371439  3.242234 -0.699097   
ёлка         1.479187  0.801772  1.560137 -0.370208  0.023535 -0.243315   
ёмкость     -0.068037  0.049069  0.001152  0.052187  0.131457 -0.198391   

                PC499     PC500  
абрамов      1.764465 -2.274053  
абсолютно    0.240191  0.121550  
авангардный -0.098801 -0.040443  
аварийка     0.242560 -0.284252  
аварийность -0.129667  0.023692  
...               ...       ...  
ярус        -0.100613 -0.065748  
яхтенный    -0.157139 -0.006504  
ящик         3.646626  2.567211  
ёлка         0.251198  1.045152  
ёмкость     -0.138920 -0.105192  

[5181 rows x 500 columns]

In [66]:
np.savetxt('data/embeddings.tsv', reduced_embeddings_df)

In [67]:
filtered_texts = [[element for element in subarray if element in dict_matrix.keys()] for subarray in lemmatized_texts]
filtered_texts

[['снег', 'дорога'],
 ['очистить', 'кабельный', 'киоск', 'реклама'],
 ['просить',
  'убрать',
  'всё',
  'дерево',
  'кустарник',
  'который',
  'выйти',
  'предел',
  'газон',
  'пешеходный',
  'зона',
  'начинать',
  'подъезд',
  'подъезд',
  'фасад',
  'дом',
  'сторона',
  'ул'],
 ['наличный'],
 ['неудовлетворительный', 'состояние', 'парадный', 'надпись', 'дверь', 'этаж'],
 ['граффити'],
 ['необходимо',
  'проверить',
  'законность',
  'установка',
  'вывеска',
  'фасад',
  'мкд',
  'адрес',
  'проспект',
  'нный'],
 ['случай',
  'вывеска',
  'установить',
  'незаконно',
  'необходимо',
  'демонтировать'],
 ['уборка', 'производиться', 'лестница', 'очень', 'грязно'],
 ['весь', 'этаж', 'вплоть', 'го'],
 ['звонок', 'жкс', 'дать', 'результат'],
 ['мусор'],
 ['отсутствовать', 'освещение', 'лестничный', 'площадка', 'этаж', 'парадный'],
 ['делать', 'благоустройство', 'никто', 'убирать', 'мусор'],
 ['ежедневно'],
 ['просьба', 'закрасить'],
 ['реклама', 'забор'],
 ['снег', 'тротуар', 'убрат

Создадим features+target массив с окном, равным 2:

In [83]:
filtered_texts

[['снег', 'дорога'],
 ['очистить', 'кабельный', 'киоск', 'реклама'],
 ['просить',
  'убрать',
  'всё',
  'дерево',
  'кустарник',
  'который',
  'выйти',
  'предел',
  'газон',
  'пешеходный',
  'зона',
  'начинать',
  'подъезд',
  'подъезд',
  'фасад',
  'дом',
  'сторона',
  'ул'],
 ['наличный'],
 ['неудовлетворительный', 'состояние', 'парадный', 'надпись', 'дверь', 'этаж'],
 ['граффити'],
 ['необходимо',
  'проверить',
  'законность',
  'установка',
  'вывеска',
  'фасад',
  'мкд',
  'адрес',
  'проспект',
  'нный'],
 ['случай',
  'вывеска',
  'установить',
  'незаконно',
  'необходимо',
  'демонтировать'],
 ['уборка', 'производиться', 'лестница', 'очень', 'грязно'],
 ['весь', 'этаж', 'вплоть', 'го'],
 ['звонок', 'жкс', 'дать', 'результат'],
 ['мусор'],
 ['отсутствовать', 'освещение', 'лестничный', 'площадка', 'этаж', 'парадный'],
 ['делать', 'благоустройство', 'никто', 'убирать', 'мусор'],
 ['ежедневно'],
 ['просьба', 'закрасить'],
 ['реклама', 'забор'],
 ['снег', 'тротуар', 'убрат

In [99]:
import random

def slice_context(array, window=2):
    result = []
    
    for sub_array in array:
        print(sub_array)
        # to make sure there is no arrays with len<5 (if window=2) 
        for i in range(len(sub_array) - window*2): 
            slice_segment = sub_array[i:i + window*2+1]
            center_element = slice_segment[window]
            other_elements = slice_segment[:window] + slice_segment[window+1:]
            # print(slice_segment)
            # print(center_element)
            # print(other_elements)
            
            result.append([other_elements, center_element])

    return result

context_target_array = slice_context(filtered_texts)

# random.shuffle(context_array)
context_target_array

['снег', 'дорога']
['очистить', 'кабельный', 'киоск', 'реклама']
['просить', 'убрать', 'всё', 'дерево', 'кустарник', 'который', 'выйти', 'предел', 'газон', 'пешеходный', 'зона', 'начинать', 'подъезд', 'подъезд', 'фасад', 'дом', 'сторона', 'ул']
['наличный']
['неудовлетворительный', 'состояние', 'парадный', 'надпись', 'дверь', 'этаж']
['граффити']
['необходимо', 'проверить', 'законность', 'установка', 'вывеска', 'фасад', 'мкд', 'адрес', 'проспект', 'нный']
['случай', 'вывеска', 'установить', 'незаконно', 'необходимо', 'демонтировать']
['уборка', 'производиться', 'лестница', 'очень', 'грязно']
['весь', 'этаж', 'вплоть', 'го']
['звонок', 'жкс', 'дать', 'результат']
['мусор']
['отсутствовать', 'освещение', 'лестничный', 'площадка', 'этаж', 'парадный']
['делать', 'благоустройство', 'никто', 'убирать', 'мусор']
['ежедневно']
['просьба', 'закрасить']
['реклама', 'забор']
['снег', 'тротуар', 'убрать']
['проблема', 'регулярный', 'вывоз', 'мусор']
['рисунок']
['пожалуйста', 'удалить', 'бетонный'

[[['просить', 'убрать', 'дерево', 'кустарник'], 'всё'],
 [['убрать', 'всё', 'кустарник', 'который'], 'дерево'],
 [['всё', 'дерево', 'который', 'выйти'], 'кустарник'],
 [['дерево', 'кустарник', 'выйти', 'предел'], 'который'],
 [['кустарник', 'который', 'предел', 'газон'], 'выйти'],
 [['который', 'выйти', 'газон', 'пешеходный'], 'предел'],
 [['выйти', 'предел', 'пешеходный', 'зона'], 'газон'],
 [['предел', 'газон', 'зона', 'начинать'], 'пешеходный'],
 [['газон', 'пешеходный', 'начинать', 'подъезд'], 'зона'],
 [['пешеходный', 'зона', 'подъезд', 'подъезд'], 'начинать'],
 [['зона', 'начинать', 'подъезд', 'фасад'], 'подъезд'],
 [['начинать', 'подъезд', 'фасад', 'дом'], 'подъезд'],
 [['подъезд', 'подъезд', 'дом', 'сторона'], 'фасад'],
 [['подъезд', 'фасад', 'сторона', 'ул'], 'дом'],
 [['неудовлетворительный', 'состояние', 'надпись', 'дверь'], 'парадный'],
 [['состояние', 'парадный', 'дверь', 'этаж'], 'надпись'],
 [['необходимо', 'проверить', 'установка', 'вывеска'], 'законность'],
 [['провери

In [ ]:
# id, element
vocab = {i: item for i, item in enumerate(dict_matrix.keys())}
# element, id
reverse_vocab = {item: i for i, item in enumerate(dict_matrix.keys())}

In [90]:
reverse_vocab

{'абрамов': 0,
 'абсолютно': 1,
 'авангардный': 2,
 'аварийка': 3,
 'аварийность': 4,
 'аварийный': 5,
 'авария': 6,
 'август': 7,
 'авиаконструктор': 8,
 'авиатор': 9,
 'авиационный': 10,
 'аврора': 11,
 'авто': 12,
 'автобус': 13,
 'автобусный': 14,
 'автовладелец': 15,
 'автолюбитель': 16,
 'автомат': 17,
 'автоматически': 18,
 'автоматический': 19,
 'автомашина': 20,
 'автомобилист': 21,
 'автомобиль': 22,
 'автомобильный': 23,
 'автостоянка': 24,
 'автотранспорт': 25,
 'автотранспортный': 26,
 'автохлам': 27,
 'агротехнический': 28,
 'адекватный': 29,
 'административный': 30,
 'администрация': 31,
 'адмирал': 32,
 'адмиралтейский': 33,
 'адрес': 34,
 'адресация': 35,
 'адресный': 36,
 'аж': 37,
 'азс': 38,
 'академик': 39,
 'академический': 40,
 'аккуратно': 41,
 'аккуратный': 42,
 'акт': 43,
 'активно': 44,
 'активный': 45,
 'актуализировать': 46,
 'актуальный': 47,
 'александр': 48,
 'александровский': 49,
 'алкоголь': 50,
 'алкогольный': 51,
 'аллея': 52,
 'алтайский': 53,
 'ал

In [88]:
reduced_embeddings_df.shape

(5181, 500)

In [ ]:
torch.cuda.is_available()


True

In [ ]:
for context, target in context_target_array:
    # print(context)
    if ["нужно", "убрать", "дорога", "срочно"] == context: print(context)

In [112]:
reduced_embeddings_df

PC1       PC2       PC3       PC4       PC5       PC6  \
абрамов     -2.167824  2.774128  0.645414  0.706883  0.687338  0.293411   
абсолютно   -1.888483  0.634621  0.358485  0.254213  0.633303 -0.763772   
авангардный -2.881359  1.788439  0.684032  0.676496 -0.199972  0.046706   
аварийка    -2.056758  0.628170 -0.414661 -0.676322  0.056741 -0.801389   
аварийность -2.465457  1.015577  0.035589  0.051802 -0.007631  0.157161   
...               ...       ...       ...       ...       ...       ...   
ярус        -3.094438  1.546435  0.613532  0.769581 -0.096623 -0.032368   
яхтенный    -2.259362  2.190666  0.732127  0.650516 -0.194278  0.029297   
ящик         9.503228 -7.857116 -3.291486  3.487890  0.656322  3.872341   
ёлка        -2.539037  0.866410  1.201623  0.396024  0.201870 -0.687713   
ёмкость     -2.975393  1.386039  0.745034  0.703419 -0.039945 -0.075109   

                  PC7       PC8       PC9      PC10  ...     PC491     PC492  \
абрамов     -0.232899  0.125882 -0.287602 -0.059639  ...  0.972674  2.503852   
абсолютно   -0.535447  0.194019  0.088726  0.054934  ... -0.030936 -0.162939   
авангардный -0.284402  0.248382 -0.170754 -0.373056  ...  0.057042 -0.005532   
аварийка    -0.582756 -0.359424 -0.020087 -0.568436  ...  0.451848 -1.177414   
аварийность -0.549549  1.115635 -0.367755 -0.895193  ...  0.134774 -0.073004   
...               ...       ...       ...       ...  ...       ...       ...   
ярус        -0.398061  0.226858 -0.154609 -0.564978  ...  0.045530  0.010797   
яхтенный    -0.254020  0.331956 -0.137822 -0.193887  ...  0.043502 -0.056493   
ящик         1.802491 -1.087298  0.220229  0.767087  ...  2.055722 -0.379162   
ёлка         1.072599  1.013498  0.049853 -1.142083  ...  0.190056  0.288682   
ёмкость     -0.072402  0.182207 -0.022567 -0.632771  ... -0.020177  0.014617   

                PC493     PC494     PC495     PC496     PC497     PC498  \
абрамов     -1.011024  2.455147  0.830435 -1.844252 -1.034388  0.631703   
абсолютно   -0.202108  0.191390 -0.130308  0.201746  0.220459 -0.469843   
авангардный -0.116463 -0.016490  0.016316  0.058177  0.000926 -0.129403   
аварийка     1.153140 -0.445216 -0.392335 -1.180905  0.580129 -0.500308   
аварийность -0.154872  0.175023  0.280558  0.380537 -0.115484 -0.096024   
...               ...       ...       ...       ...       ...       ...   
ярус        -0.072109  0.012238  0.021080  0.072358  0.026876 -0.088743   
яхтенный    -0.227974 -0.036700  0.090807  0.148753  0.051623 -0.173419   
ящик        -2.129037 -4.887692 -4.453293  0.371439  3.242234 -0.699097   
ёлка         1.479187  0.801772  1.560137 -0.370208  0.023535 -0.243315   
ёмкость     -0.068037  0.049069  0.001152  0.052187  0.131457 -0.198391   

                PC499     PC500  
абрамов      1.764465 -2.274053  
абсолютно    0.240191  0.121550  
авангардный -0.098801 -0.040443  
аварийка     0.242560 -0.284252  
аварийность -0.129667  0.023692  
...               ...       ...  
ярус        -0.100613 -0.065748  
яхтенный    -0.157139 -0.006504  
ящик         3.646626  2.567211  
ёлка         0.251198  1.045152  
ёмкость     -0.138920 -0.105192  

[5181 rows x 500 columns]

In [124]:
reduced_embeddings_df.iloc[[3590, 4699, 821, 1708]].to_numpy().mean(axis=0)

array([ 4.41013627e+01, -4.41969689e+01,  3.39607274e+00, -5.41751068e+01,
        1.28451568e+01,  6.78237490e+01, -4.18689589e+00,  5.53137204e+01,
       -1.07695220e+01, -3.09442781e+00, -1.83393072e+01, -1.07797913e+01,
        4.87821942e+00, -6.42730550e+00, -6.47168785e+00, -2.26760176e+01,
        7.68497778e+00,  3.35399016e+00, -2.61929370e+01, -1.31393732e+01,
       -1.72778225e+01, -6.61872064e+00,  4.87934277e+01, -1.78846774e+01,
       -1.22923884e+01, -3.82167473e+01,  2.99990263e+01,  8.80261412e+00,
       -4.99774074e+00,  2.83469586e+00,  1.13213454e+01, -4.54868159e-02,
       -6.60033277e+00, -6.87470072e-01,  4.54504628e+01,  1.93773102e+01,
        2.53389129e+01, -5.03672233e+00,  9.07556435e+00, -2.32256175e+01,
        1.11847946e+01, -7.94925072e+00, -1.52782934e+00, -5.34642094e+00,
        9.16287212e+00, -9.36211420e+00, -1.78439198e+01,  1.00216992e+00,
       -8.55116042e+00,  6.35931336e-01,  4.43113094e+00, -1.57540904e+01,
        1.63462918e+01,  

In [126]:
reduced_embeddings_df.shape

(5181, 500)

In [125]:
for context, target in context_target_array:
    # print(context)
    # if ["нужно", "убрать", "дорога", "срочно"] == context: print(context)
    context_indices = [reverse_vocab[word] for word in context]
    print(context_indices)
    print(torch.tensor(reduced_embeddings_df.iloc[context_indices].to_numpy()).mean(dim=0).shape)
    break

[3590, 4699, 821, 1708]
torch.Size([500])


In [ ]:
import torch
from torch import nn, optim

class CBOW(nn.Module):
    def __init__(self, embeddings):
        super(CBOW, self).__init__()
        self.embeddings = embeddings
        self.fc = nn.Linear(self.embeddings.shape[1], self.embeddings.shape[0])

    def forward(self, context_indices):
        embeds = torch.tensor(torch.tensor(self.embeddings.iloc[context_indices].to_numpy()).mean(dim=0).view(1, -1), dtype=torch.float32, device='cuda:0')
        out = self.fc(embeds)
        return out

def train_model(model, data, epochs=50, learning_rate=0.001):
    optimizer = optim.Adam(model.parameters(), lr=learning_rate) 
    loss_function = nn.CrossEntropyLoss()

    
    for epoch in range(epochs):
        loss_sum = 0
        for context, target in data:
            model.zero_grad()

            # Преобразование в индексы
            context_indices = [reverse_vocab[word] for word in context]
            target_indices = torch.tensor([reverse_vocab[target]], dtype=torch.long, device='cuda:0')

            output = model(context_indices)
            # print(output)
            # print(target_indices)
            # break
            loss = loss_function(output, target_indices)
            loss.backward()
            optimizer.step()

            loss_sum += loss.item()

        print(f'Epoch [{epoch + 1}/{epochs}], Loss: {loss_sum:.4f}')

def predict(model, context):
    context_indices = torch.tensor([reverse_vocab[word] for word in context], dtype=torch.long)
    with torch.no_grad():
        output = model(context_indices)
        predicted_index = torch.argmax(output, dim=1).item()
        return vocab[predicted_index]


model = CBOW(reduced_embeddings_df)

device = torch.device('cuda')
model.to(device)

train_model(model, context_target_array[:5000])


context_example = ["нужно", "убрать", "дорога", "срочно"]
predicted_word = predict(model, context_example)
print(f"Предсказанное слово для контекста {context_example}: {predicted_word}")

C:\Users\gunte\AppData\Local\Temp\ipykernel_7256\2627974423.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  embeds = torch.tensor(torch.tensor(self.embeddings.iloc[context_indices].to_numpy()).mean(dim=0).view(1, -1), dtype=torch.float32, device='cuda:0')


Epoch [1/50], Loss: 70364.4371
Epoch [2/50], Loss: 44240.2704
Epoch [3/50], Loss: 34872.1832
Epoch [4/50], Loss: 28377.9253
Epoch [5/50], Loss: 24865.2444
Epoch [6/50], Loss: 21892.5396
Epoch [7/50], Loss: 18545.5960
Epoch [8/50], Loss: 16268.4772
Epoch [9/50], Loss: 15516.4175
Epoch [10/50], Loss: 14006.6627
Epoch [11/50], Loss: 12679.8076
Epoch [12/50], Loss: 11709.2736
Epoch [13/50], Loss: 10267.4957
Epoch [14/50], Loss: 10530.0038
Epoch [15/50], Loss: 9341.6371
Epoch [16/50], Loss: 8734.9770
Epoch [17/50], Loss: 8464.4878
Epoch [18/50], Loss: 8223.1045
Epoch [19/50], Loss: 7538.6888
Epoch [20/50], Loss: 7065.6412
Epoch [21/50], Loss: 7280.6701
Epoch [22/50], Loss: 7094.2404
Epoch [23/50], Loss: 6405.7007
Epoch [24/50], Loss: 6154.5085
Epoch [25/50], Loss: 5813.3379
Epoch [26/50], Loss: 5846.6265
Epoch [27/50], Loss: 5761.6328
Epoch [28/50], Loss: 5082.8930
Epoch [29/50], Loss: 5143.3919
Epoch [30/50], Loss: 4996.3036
Epoch [31/50], Loss: 4938.7894
Epoch [32/50], Loss: 4761.8093
Epo

In [110]:
context_example = ["убрать", "подъезд", "пятница", "срочно"]
predicted_word = predict(model, context_example)
predicted_word

C:\Users\gunte\AppData\Local\Temp\ipykernel_7256\2627974423.py:12: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  embeds = torch.tensor(torch.tensor(self.embeddings.iloc[context_indices].to_numpy()).mean(dim=0).view(1, -1), dtype=torch.float32, device='cuda:0')


'песок'